**Dividend+ value Investing  Strategy**

- Dividend Yield > 2  
- Dividend 5 Year Average > 1%  
- EPS 5 Year Avg > 8%  
- Price to Book < 1.2  
- Sales 5 Year Avg > 3%  
- Payout Ratio < 60  
- P/E (This Year's Estimate) Less than or Equal to 25.0  
- EPS Growth (Proj This Quarter vs. Same Quarter Prior Yr) Highest 20% for industry (pred)  
- EPS Growth (Proj this Yr vs. Last Yr) Highest 20% for industry (pred)  

**Undervalued stock**
- Trailing P/E: 0 - 20  
- Price / Earnings to Growth (P/E/G): < 1, 1 yr.  
- % Change in EPS (Basic): 25% to 50% and 50% to 100% and > 100%  

In [354]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import requests
from datetime import datetime
import time

In [392]:
fh_key = 'bt3efpf48v6tfcs816eg'
fm_key = '8a1cf9d14d53126b05c8a7636fe3d006'

SP = requests.get(f'https://financialmodelingprep.com/api/v3/sp500_constituent?&apikey={fm_key}').json()    
SP = pd.DataFrame(SP)
sp = SP['symbol'].values.tolist()
NASDAQ = requests.get(f'https://financialmodelingprep.com/api/v3/nasdaq_constituent?&apikey={fm_key}').json()
NASDAQ = pd.DataFrame(NASDAQ)
nasdaq = NASDAQ['symbol'].values.tolist()
DJI = requests.get(f'https://financialmodelingprep.com/api/v3/dowjones_constituent?&apikey={fm_key}').json()
DJI = pd.DataFrame(DJI)
dji = DJI['symbol'].values.tolist()

tickers = sp + nasdaq + dji
tickers = np.array(tickers)
tickers = np.unique(tickers)

In [494]:
def paras(ticker):
    def tdf(data):
        return pd.DataFrame(data)
    # setup the dataframe
    # res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
    #                               'Sales_5avg', 'payoutRatio', 'EPSG_Q', 'EPSG_Y', 'PE_est',\
    #                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])
    res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
                                  'Sales_5avg', 'payoutRatio', 'PE_est',\
                                  'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])

    today = datetime.now().strftime("%d/%m/%Y %H:%M:%S")
    res = res.append({'Date': today}, ignore_index=True)
    res = res.set_index('Date')

    res.loc[today, 'symbol'] = ticker

    try:
        ratios = requests.get(f'https://financialmodelingprep.com/api/v3/ratios/{ticker}?limit=5&apikey={fm_key}').json()
        rs = ['dividendYield', 'priceToBookRatio', 'payoutRatio', 'priceEarningsRatio', 'priceEarningsToGrowthRatio']
        if len(ratios) == 0:
            for i in rs:
                res.loc[today, i] = np.nan       
            res.loc[today, 'DY_5avg'] = np.nan
        else:
            for i in rs:
                res.loc[today, i] = ratios[0][i]   
            ratios_temp = pd.DataFrame(ratios)
            res.loc[today, 'DY_5avg'] = np.mean(ratios_temp.loc[:,'dividendYield'])
    except:
        for i in rs:
            res.loc[today, i] = np.nan       
        res.loc[today, 'DY_5avg'] = np.nan
        
    try:
        is_growth = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-growth/{ticker}?apikey={fm_key}&limit=40').json()
        if len(is_growth) < 5:
            res.loc[today, 'EPS_5avg'] = np.nan
            res.loc[today, 'Sales_5avg'] = np.nan
        else:
            is_growth = tdf(is_growth)
            res.loc[today, 'EPS_5avg'] = np.mean(is_growth.growthEPS[:5])
            res.loc[today, 'Sales_5avg'] = np.mean(is_growth.growthRevenue[:5])
    except:
        res.loc[today, 'EPS_5avg'] = np.nan
        res.loc[today, 'Sales_5avg'] = np.nan
    
    try:
        ttms = requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={fm_key}').json()
        if len(ttms) == 1:
            ttms = tdf(ttms)
            res.loc[today, 'Trailing_PE'] = ttms.priceEarningsRatioTTM.item()
        else: 
            res.loc[today, 'Trailing_PE'] = np.nan
    except:
        res.loc[today, 'Trailing_PE'] = np.nan
    
    try:
        fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=2&apikey={fm_key}').json()
        if len(fgrowth) == 0:
            res.loc[today, 'EPS_d'] = np.nan
        else:
            res.loc[today, 'EPS_d'] = fgrowth[0]['epsgrowth']
    except:
        res.loc[today, 'EPS_d'] = np.nan
    
    try:
        cp = requests.get(f'https://financialmodelingprep.com/api/v3/quote/{ticker}?apikey={fm_key}').json()
        if len(cp) == 0:
            cp = np.nan
        else:
            cp = cp[0]['price']
    except:
        cp = np.nan
        
    try:
        eps_est = requests.get(f'https://finnhub.io/api/v1/stock/earnings?symbol={ticker}&token={fh_key}').json()
        if len(eps_est) == 0:
            res.loc[today, 'PE_est'] = np.nan
        elif len(eps_est) != 0: 
            try:
                est = eps_est[0]['estimate']
                if est is None:
                    res.loc[today, 'PE_est'] = np.nan
                else:
                    res.loc[today, 'PE_est'] = cp / eps_est[0]['estimate']
            except:
                res.loc[today, 'PE_est'] = np.nan
    except:
        res.loc[today, 'PE_est'] = np.nan

    return res

In [495]:
def dvscreener(ticker):
    ps = paras(ticker)
    ps = ps.fillna(value = np.nan)
    nn = sum(ps.isna().iloc[0,:])
    if (nn == 0) & (ps.dividendYield.item() > 0.02) & (ps.DY_5avg.item() > 0.01)\
    & (ps.EPS_5avg.item() > 0.08) & (ps.priceToBookRatio.item() < 1.2)\
    & (ps.Sales_5avg.item() > 0.03) & (ps.payoutRatio.item() < 0.6) & (ps.PE_est.item() <= 25.0):
        return True
    else:
        return False

def undervalue(ticker):
    ps = paras(ticker)
    ps = ps.fillna(value = np.nan)
    nn = sum(ps.isna().iloc[0,:])
    if (nn == 0) & (0 < ps.Trailing_PE.item() < 20) & (ps.priceEarningsToGrowthRatio.item() < 1)\
    & (0.25 < ps.EPS_d.item() < 0.5):
        return True
    else:
        return False

In [489]:
valid = []
n = 13
groups = np.array_split(tickers, n)
for group in groups:
    for ticker in group:
        if dvscreener(ticker):
            valid.append(ticker)
    time.sleep(60)

valid

In [403]:
undervalued = []
n = 15
groups = np.array_split(tickers, n)
for group in groups:
    for ticker in group:
        if undervalue(ticker):
            undervalued.append(ticker)
    time.sleep(60)

undervalued

['ADM',
 'AON',
 'DHI',
 'HII',
 'HUM',
 'IVZ',
 'K',
 'LEN',
 'MAS',
 'MS',
 'NOC',
 'ORCL',
 'PGR',
 'PHM',
 'PNC',
 'TROW']

# Draft

In [287]:
# def tdf(data):
#     return pd.DataFrame(data)

# # setup the dataframe
# # res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
# #                               'Sales_5avg', 'payoutRatio', 'EPSG_Q', 'EPSG_Y', 'PE_est',\
# #                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])
# res = pd.DataFrame(columns = ['Date', 'symbol', 'dividendYield', 'DY_5avg', 'EPS_5avg', 'priceToBookRatio',\
#                               'Sales_5avg', 'payoutRatio', 'PE_est',\
#                               'priceEarningsRatio',  'Trailing_PE', 'priceEarningsToGrowthRatio', 'EPS_d'])

# today = datetime.now().strftime("%d/%m/%Y %H:%M:%S")
# res = res.append({'Date': today}, ignore_index=True)
# res = res.set_index('Date')

# res.loc[today, 'symbol'] = ticker

# ratios = requests.get(f'https://financialmodelingprep.com/api/v3/ratios/{ticker}?limit=5&apikey={fm_key}').json()
# rs = ['dividendYield', 'priceToBookRatio', 'payoutRatio', 'priceEarningsRatio', 'priceEarningsToGrowthRatio']
# # eps = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-as-reported/{ticker}?limit=5&apikey={fm_key}').json()    
# # eps_temp = tdf(eps)
# # res.loc[today, 'EPS_5avg'] = np.mean(eps_temp.loc[:, 'earningspersharebasic'])
# is_growth = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-growth/{ticker}?apikey={fm_key}&limit=40').json()
# is_growth = tdf(is_growth)
# ttms = requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={fm_key}').json()
# ttms = tdf(ttms)
# fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=2&apikey={fm_key}').json()
# # current price
# cp = requests.get(f'https://financialmodelingprep.com/api/v3/quote/{ticker}?apikey={fm_key}').json()[0]['price']

# for i in rs:
#     res.loc[today, i] = ratios[0][i]
# ratios_temp = pd.DataFrame(ratios)

# res.loc[today, 'DY_5avg'] = np.mean(ratios_temp.loc[:,'dividendYield'])

# res.loc[today, 'EPS_5avg'] = np.mean(is_growth.growthEPS[:5])

# res.loc[today, 'Sales_5avg'] = np.mean(is_growth.growthRevenue[:5])

# res.loc[today, 'Trailing_PE'] = ttms.priceEarningsRatioTTM.item()

# res.loc[today, 'EPS_d'] = fgrowth[0]['epsgrowth']

# # res.loc[today, 'EPS_d'] = (eps_temp.loc[0, 'earningspersharebasic']\
# #                            - eps_temp.loc[1, 'earningspersharebasic'])/ eps_temp.loc[1, 'earningspersharebasic']

# eps_est = requests.get(f'https://finnhub.io/api/v1/stock/earnings?symbol={ticker}&token={fh_key}').json()
# res.loc[today, 'PE_est'] = cp / eps_est[0]['estimate']

# res

In [288]:
# eps = requests.get(f'https://financialmodelingprep.com/api/v3/income-statement-as-reported/{ticker}?limit=5&apikey={fm_key}').json()
# eps = pd.DataFrame(eps)
# eps.loc[:,['date', 'earningspersharebasic']]

In [289]:
# fgrowth = requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?limit=5&apikey={fm_key}').json()
# # fgrowth[0]['epsgrowth']
# fgrowth = pd.DataFrame(fgrowth)
# fgrowth.loc[:,['date', 'epsgrowth']]

In [290]:
# # r = requests.get(f'https://finnhub.io/api/v1/stock/financials-reported?symbol={ticker}&token={fh_key}').json()
# # pd.DataFrame(r['data'][1]['report']['ic'])
# eps.earningspersharebasic.pct_change(-1)

In [405]:
# len(undervalued)

In [426]:
ast = requests.get(f'https://finnhub.io/api/v1/stock/symbol?exchange=US&token={fh_key}').json()
ast = pd.DataFrame(ast)['symbol'].tolist()

In [509]:
# def test():
#     test = []
#     n = int(len(ast[0:300])/300) + 1
#     groups_test = np.array_split(ast[0:300], n)
#     c = 0
#     for group in groups_test:
#         for ticker in group:
#             c = c+1
#             print(ticker, c)
#             if dvscreener(ticker):
#                 test.append(ticker)
#         time.sleep(60)

#     return test

In [510]:
# t = test()

GNTW 1
HNGGF 2
EUCG 3
EPRCY 4
TKAMY 5
SPPGF 6
RPAR 7
ACOPY 8
PEXXF 9
AEGOF 10
NUEC 11
TRMB 12
BDC 13
TRST 14
VIGI 15
APNHF 16
EWO 17
DTIL 18
MIN 19
ISVIF 20
ZKPLF 21
OSH 22
IQDY 23
LSTYF 24
KNOP 25
DDCCF 26
FFCNF 27
SMDRF 28
NEP 29
RETA 30
AKORF 31
RODN 32
ISCV 33
BICEF 34
ZAZA 35
JGSMY 36
FUTS 37
CYDX 38
LILAK 39
LOB 40
DMPLF 41
SGRRF 42
IVW 43
SHVTF 44
PCSA 45
ESCNF 46
PMMOF 47
MNGGF 48
CYVF 49
ISGN 50
RXN 51
FUWAF 52
QARP 53
SAFT 54
QGRSF 55
RYF 56
MMEXD 57
MYTAY 58
XPPLF 59
GLAD 60
ACNE 61
ACGI 62
PTMN 63
FXLG 64
SEBNF 65
HNFSB 66
SSREY 67
SEHCF 68
TOPPY 69
PIOE 70
RH 71
USFD 72
BBN 73
TRUE 74
EFV 75
OCCIO 76
WRB.PRF 77
IVHI 78
PCLB 79
IVVI 80
RTPYU 81
BSN.WS 82
GNK 83
LGO 84
PTVE 85
GBGR 86
EVGRF 87
HARL 88
VOYT 89
LAIX 90
VS 91
OMMH 92
CNSRF 93
HGH 94
IBHF 95
STVGF 96
SUPIF 97
BLFE 98
FSZ 99
AEVIF 100
DHYAF 101
AXIM 102
AIQUY 103
MSGM 104
ZG 105
OJSCY 106
ZION 107
SGHIY 108
PAKTY 109
SHZNF 110
BMRN 111
SNII.U 112
AGPL 113
BLRDY 114
SCHZ 115
HCMC 116
SGAMF 117
OILRF 118
TMHTY 119


In [511]:
# t

['GNK']

In [512]:
# paras('GNK')

symbol dividendYield    DY_5avg  EPS_5avg  \
Date                                                            
22/07/2021 16:33:46    GNK     0.0296904  0.0452524  0.432158   

                    priceToBookRatio Sales_5avg payoutRatio   PE_est  \
Date                                                                   
22/07/2021 16:33:46         0.445179   0.230511  -0.0436533  24.1749   

                    priceEarningsRatio Trailing_PE priceEarningsToGrowthRatio  \
Date                                                                            
22/07/2021 16:33:46           -1.47028    -7.14755                -0.00485113   

                      EPS_d  
Date                         
22/07/2021 16:33:46  3.0308